# Tap Testing, Day 3

Read through this document to complete the Day 3 activity. By the time you load this file, you should have already created some audio recordings in the `.wav` file format. Make sure you have those files ready to upload - this code is going to help you analyze them using the power of computing and mathematics.

### About Sound Waves

Sound waves, if you have never read about them before, are regions of high and low pressure moving through the air. Simple sound waves have one **frequency** (how many times the high-pressure part happens each second). Sound waves also have an **amplitude**, or the amount of energy difference between high and low pressures. Sounds that we hear are usually much more complex than just a single frequency, however. To explore sound waves, try the tool here which allows you to blend up to 3 different frequencies together. 440 Hz, 555 Hz, and 660 Hz create an A-major chord in music! But as you investigate blending different frequencies, consider: can you tell just by looking at the plot what frequencies are represented?

#### How to Use:

1. **Run the Code Cell**:
   - Hover over the cell of code below to reveal a run (play) button. Press the run button to execute the code. Adjust the sliders and press the **Show** button below them. Try the default frequencies first: with just one, then with two of them, then all three. Then, try altering the frequencies and amplitudes more. You can also play the audio created by these overlapping frequencies by pressing the play button on the audio player just below the graph.


In [ ]:
# Import necessary libraries
import numpy as np
import matplotlib.pyplot as plt
import ipywidgets as widgets
from IPython.display import display, Audio, clear_output

# Function to generate the waveform for plotting
def generate_waveform(num_waves, frequencies, amplitudes, duration_ms, sample_rate=44100):
    t = np.linspace(0, duration_ms / 1000, sample_rate * duration_ms // 1000)  # Sampling rate based on duration
    y = np.zeros_like(t)
    for i in range(num_waves):
        y += amplitudes[i] * np.sin(2 * np.pi * frequencies[i] * t)
    y /= np.max(np.abs(y))  # Normalize to -1 to 1
    return t * 1000, y  # Convert time back to milliseconds for display

# Function to generate the waveform for audio
def generate_audio_waveform(num_waves, frequencies, amplitudes, sample_rate=44100, duration=1):
    t = np.linspace(0, duration, sample_rate * duration)  # 1-second duration
    y = np.zeros_like(t)
    for i in range(num_waves):
        y += amplitudes[i] * np.sin(2 * np.pi * frequencies[i] * t)
    y /= np.max(np.abs(y))  # Normalize to -1 to 1
    return y

# Function to update the plot
def update_plot(num_waves, f1, f2, f3, a1, a2, a3, duration_ms):
    frequencies = [f1, f2, f3][:num_waves]
    amplitudes = [a1, a2, a3][:num_waves]
    t, y = generate_waveform(num_waves, frequencies, amplitudes, duration_ms)

    plt.figure(figsize=(10, 6))
    plt.plot(t, y, label='Waveform')
    plt.title('Blending multiple frequencies')
    plt.xlabel('Time (ms)')
    plt.ylabel('Amplitude')
    plt.ylim(-1, 1)  # Set the amplitude range from -1 to 1
    plt.grid(True)

    # Generate legend text
    legend_text = ' + '.join([f'{freq:.1f} Hz, amplitude of {amp:.1f}' for freq, amp in zip(frequencies, amplitudes)])
    plt.figtext(0.5, -0.05, legend_text, ha='center', va='top', fontsize=15)  # Adjusted font size

    plt.show()

    return frequencies, amplitudes, duration_ms

# Function to play the audio
def play_audio(frequencies, amplitudes):
    y = generate_audio_waveform(len(frequencies), frequencies, amplitudes)
    display(Audio(y, rate=44100))
    display(widgets.HTML(value="<p>Click play to listen to the resulting sound!</p>"))

# Create sliders for interactivity
num_waves_slider = widgets.IntSlider(min=1, max=3, step=1, value=1, description='Number of Waves')
f1_slider = widgets.FloatSlider(min=100, max=1000, step=10, value=440, description='Frequency 1 (Hz)')
f2_slider = widgets.FloatSlider(min=100, max=1000, step=10, value=555, description='Frequency 2 (Hz)')
f3_slider = widgets.FloatSlider(min=100, max=1000, step=10, value=660, description='Frequency 3 (Hz)')
a1_slider = widgets.FloatSlider(min=0.1, max=1, step=0.1, value=0.5, description='Amplitude 1')
a2_slider = widgets.FloatSlider(min=0.1, max=1, step=0.1, value=0.5, description='Amplitude 2')
a3_slider = widgets.FloatSlider(min=0.1, max=1, step=0.1, value=0.5, description='Amplitude 3')
duration_slider = widgets.IntSlider(min=1, max=1000, step=5, value=5, description='Duration (ms)')

# Button to show plot and play audio
show_button = widgets.Button(description="Show")
output = widgets.Output()

def on_button_clicked(b):
    with output:
        clear_output(wait=True)
        frequencies, amplitudes, duration_ms = update_plot(num_waves_slider.value, f1_slider.value, f2_slider.value, f3_slider.value, a1_slider.value, a2_slider.value, a3_slider.value, duration_slider.value)
        play_audio(frequencies, amplitudes)

show_button.on_click(on_button_clicked)

# Combine sliders and button into a single interface
ui = widgets.VBox([num_waves_slider, f1_slider, f2_slider, f3_slider, a1_slider, a2_slider, a3_slider, duration_slider, show_button, output])

# Display the interactive plot and sliders
display(ui)


### Step 0: Environment Preparation

In this step, we will prepare the environment by installing necessary Python libraries. These libraries provide the functionality needed to process and analyze the audio files. Each library has a specific role in the processing pipeline:

- **pydub**: This library is used for audio processing tasks such as loading and manipulating audio files.
- **scipy**: The scipy library is essential for scientific and technical computing, particularly for performing the Fast Fourier Transform (FFT).
- **matplotlib**: This library is used for creating visualizations, such as plotting waveforms and frequency spectrums.
- **numpy**: A fundamental package for numerical computations in Python, numpy is used for handling arrays and performing mathematical operations.

#### How to Use:

1. **Run the Code Cell**:
   - Hover over the cell of code below, causing a run (play) button to appear.  Press the run button to run the code. This will ensure that all required Python libraries are installed and ready for use in subsequent steps.


In [ ]:
# Run this code cell first, to ensure that appropriate Python libraries are installed
!pip install pydub scipy matplotlib numpy

### Step 1: Find Tap Segments in Audio Files

In this step, we will process all `.wav` files in the current directory containing repeated sounds of someone tapping a wooden block with a hammer. Each tap sound is detected based on amplitude spikes and extracted into individual 5ms segments. The segments are then normalized and saved as separate `.wav` files along with corresponding waveform images.

#### How to Use:

1. **Prepare Your Directory**:
   - Ensure your `.wav` files are placed in the current working directory of the notebook. This is typically the default directory opened in Google Colab.

2. **Run the Code Cell**:
   - Execute the code cell below to process the audio files.

#### Explanation of Parameters:

- **THRESHOLD**: The amplitude threshold for detecting tap sounds. Setting this value higher will make the detection stricter, only detecting louder taps.
- **MIN_DISTANCE_MS**: The minimum distance between consecutive spikes in milliseconds. This helps to ensure that each detected tap is distinct.
- **PRE_SPIKE_MS**: The time in milliseconds before each detected spike to begin the segment. This helps capture the initial part of the tap sound.
- **SEGMENT_LENGTH_MS**: The length of each segment in milliseconds. This defines how long each extracted segment will be.

#### Explanation of the Process:

The code will first load each `.wav` file and detect the high amplitude spikes representing tap sounds. It will then extract segments starting a short time before each detected spike, normalize the segments for consistent amplitude, and save them as individual `.wav` files along with waveform images. The state of each file is tracked using a JSON file to avoid reprocessing.

Normalization ensures that each audio segment has a consistent amplitude level, making it easier to compare segments and analyze the tap sounds accurately.


In [ ]:
import os
import json
from pydub import AudioSegment
from scipy.io import wavfile
import numpy as np
import matplotlib.pyplot as plt

# Parameters for tap detection (adjust these values as needed)
THRESHOLD = 0.6    # Amplitude threshold for detecting tap sounds
MIN_DISTANCE_MS = 100  # Minimum distance between consecutive spikes in milliseconds
PRE_SPIKE_MS = 0.2  # Time in milliseconds before each spike to extract segments
SEGMENT_LENGTH_MS = 5  # Time in milliseconds for each segment

# Function to load a .wav file and return the audio data and sample rate
def load_wav(file_path):
    sample_rate, data = wavfile.read(file_path)

    # Convert stereo to mono if necessary
    if len(data.shape) == 2:
        data = np.mean(data, axis=1)

    return sample_rate, data

# Function to detect high amplitude spikes in the audio data
def detect_taps(data, sample_rate, threshold=THRESHOLD, min_distance_ms=MIN_DISTANCE_MS):
    min_distance = int((min_distance_ms / 1000) * sample_rate)
    normalized_data = data / np.max(np.abs(data))
    spikes = np.where(normalized_data > threshold)[0]
    filtered_spikes = []
    last_spike = -min_distance
    for spike in spikes:
        if spike - last_spike >= min_distance:
            filtered_spikes.append(spike)
            last_spike = spike
    return filtered_spikes

# Function to normalize audio segments
def normalize_audio(segment):
    segment = segment / np.max(np.abs(segment))
    return np.int16(segment * 32767)  # Convert to 16-bit PCM

# Function to extract segments starting a short time before each detected spike
def extract_tap_segments(data, sample_rate, spike_indices, pre_spike_ms=PRE_SPIKE_MS, segment_ms=SEGMENT_LENGTH_MS):
    segments = []
    pre_spike_samples = int((pre_spike_ms / 1000) * sample_rate)
    segment_samples = int((segment_ms / 1000) * sample_rate)
    for spike_index in spike_indices:
        start = max(0, spike_index - pre_spike_samples)
        end = start + segment_samples
        segment = data[start:end]
        normalized_segment = normalize_audio(segment)
        segments.append((start, normalized_segment))
    return segments

# Function to save each segment as a .wav file and plot waveform images
def save_segments(segments, sample_rate, output_folder, base_name):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
    for i, (start, segment) in enumerate(segments):
        segment_id = f"{i+1:02d}"
        segment_audio = AudioSegment(
            segment.tobytes(),
            frame_rate=sample_rate,
            sample_width=2,  # 16-bit PCM is 2 bytes
            channels=1
        )
        output_path = f"{output_folder}/{base_name}_{segment_id}.wav"
        segment_audio.export(output_path, format="wav")

        # Convert sample indices to time in milliseconds
        times = np.arange(len(segment)) * (1000.0 / sample_rate)

        # Plot waveform
        plt.figure(figsize=(10, 4))
        plt.plot(times, segment, label='Waveform')
        plt.title(f'{base_name} {segment_id}: {SEGMENT_LENGTH_MS}ms of amplitude data')
        plt.xlabel('Time (ms)')
        plt.ylabel('Amplitude')
        plt.legend()
        plt.savefig(f"{output_folder}/{base_name}_{segment_id}.png")
        plt.close()
        print(f"Tap {segment_id}: Start Sample Index {start}, Saved to {output_path}")

# Function to load the state mapping from a JSON file
def load_state(file_path):
    if os.path.exists(file_path):
        with open(file_path, 'r') as file:
            return json.load(file)
    return {}

# Function to save the state mapping to a JSON file
def save_state(file_path, state):
    with open(file_path, 'w') as file:
        json.dump(state, file, indent=4)

# Function to get the current state of all .wav files in the directory
def get_wav_files_state(directory, state_file):
    state = load_state(state_file)
    wav_files = [f for f in os.listdir(directory) if f.endswith('.wav')]
    for wav_file in wav_files:
        base_name = os.path.splitext(wav_file)[0]
        if base_name not in state:
            state[base_name] = {'state': 'non-split'}
    return state

# Main function to loop through all .wav files and process them
def process_directory(directory, state_file):
    state = get_wav_files_state(directory, state_file)
    for base_name, info in state.items():
        if info['state'] == 'non-split':
            subdir = os.path.join(directory, base_name)
            if not os.path.exists(subdir):
                os.makedirs(subdir)
                file_path = os.path.join(directory, f"{base_name}.wav")
                print(f"Processing {file_path}...")
                sample_rate, data = load_wav(file_path)
                spike_indices = detect_taps(data, sample_rate)
                segments = extract_tap_segments(data, sample_rate, spike_indices, pre_spike_ms=PRE_SPIKE_MS, segment_ms=SEGMENT_LENGTH_MS)
                print(f"Extracted {len(segments)} segments.")
                save_segments(segments, sample_rate, subdir, base_name)
                info['state'] = 'split'
                info['segments'] = [f"{i+1:02d}" for i in range(len(segments))]
                save_state(state_file, state)
            else:
                print(f"Skipping {base_name}: Subdirectory already exists.")
    save_state(state_file, state)

# Process this step
directory = '.'
state_file = 'wav_files_state.json'
process_directory(directory, state_file)


### Visualization after Step 1: Interactive Waveform Visualization

This interactive tool allows you to explore the waveform of a selected segment by hovering over individual samples to see the amplitude and time data.

#### How to Use:

1. **Set the Segment Name**:
   - Assign a value to the `SEGMENT_NAME` parameter in the code. The segment name should be in the format `base_name_segment_id`, where `base_name` is the name of the original audio file and `segment_id` is the segment number (e.g., `"sample_01"`).  Keep the quotation marks in the code!
   
   **Example**: if the segment name you wish to analyze is called `no_holes_01`, you would change the line of code involving `SEGMENT_NAME` as follows:
```python
SEGMENT_NAME = "no_holes_01"
```

2. **Run the Code**:
   - Execute the code cell to create the interactive visualization for the specified segment.

3. **View Interactive Plot**:
   - The interactive plot of the selected segment will be displayed. You can hover over the plot to navigate through the samples to see the time (in milliseconds) and amplitude values for each sample.

4. **Check Available Segments**:
   - If the specified segment name does not exist, the code will display a message and list all available segment names. You can then choose one of the listed segments and update the `SEGMENT_NAME` parameter.

By using this tool, you can gain detailed insights into the waveform of each tap sound segment, providing a comprehensive analysis of the audio data.

This interactive visualization tool leverages `plotly` to provide a user-friendly interface for exploring the segment data.

In [ ]:
import os
import json
import plotly.graph_objs as go
import plotly.express as px
from scipy.io import wavfile
import numpy as np
from IPython.display import display, HTML

# Set the SEGMENT_NAME parameter to the segment you want to explore
SEGMENT_NAME = "4C_center_01"  # Replace with the name of the segment to visualize

# Function to load the state mapping from a JSON file
def load_state(file_path):
    if os.path.exists(file_path):
        with open(file_path, 'r') as file:
            return json.load(file)
    return {}

# Function to create an interactive plot for a segment
def create_interactive_plot(segment, base_name):
    subdir = os.path.join('.', base_name)
    segment_path = os.path.join(subdir, f"{base_name}_{segment}.wav")
    sample_rate, data = wavfile.read(segment_path)

    # Check if the data is stereo and convert to mono if necessary
    if len(data.shape) == 2:
        data = np.mean(data, axis=1)

    # Normalize the data
    normalized_data = data / np.max(np.abs(data))

    # Ensure segment length matches expected length
    segment_length_ms = 5
    expected_samples = int((segment_length_ms / 1000) * sample_rate)
    if len(normalized_data) != expected_samples:
        print(f"Warning: Segment length mismatch. Expected {expected_samples} samples, got {len(normalized_data)} samples.")

    # Convert sample indices to time in milliseconds
    times = np.arange(len(normalized_data)) * (1000.0 / sample_rate)

    # Create the plot
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=times, y=normalized_data, mode='lines', name='Waveform'))

    fig.update_layout(
        title=f'{base_name} {segment}: Interactive Waveform',
        xaxis_title='Time (ms)',
        yaxis_title='Amplitude',
        hovermode='x unified'
    )

    return fig

# Function to list available segments
def list_available_segments(state):
    segments = []
    for base_name, info in state.items():
        if 'segments' in info and info['state'] == 'split':
            segments.extend([f"{base_name}_{seg}" for seg in info['segments']])
    return segments

# Main function to create the interactive plot or list available segments
def create_interactive_tool(state_file, segment_name):
    state = load_state(state_file)
    available_segments = list_available_segments(state)

    if segment_name in available_segments:
        base_name, segment_id = segment_name.rsplit('_', 1)
        fig = create_interactive_plot(segment_id, base_name)
        fig.show()
    else:
        print(f"Segment '{segment_name}' not found.")
        print("To load a segment in this visualizer, copy one of the names below and\npaste it between the quotes after SEGMENT_NAME = in the code,\nthen re-run the cell.")
        print("Available segments are:")
        for segment in available_segments:
            print(segment)

# Process this step
state_file = 'wav_files_state.json'
create_interactive_tool(state_file, SEGMENT_NAME)


### Step 2: FFT Transformation with Frequency Binning and Top 10 Display

In this step, we will perform a Fast Fourier Transform (FFT) on the segmented `.wav` files in the "split" state. The FFT will generate a set of amplitudes at different frequencies present in each file. We will then bin these frequencies into defined ranges and save the entire range of bins into individual JSON files for each sub-file. Additionally, we will display the top 10 frequencies in a simplified FFT graph and save these top 10 frequencies in the overall JSON file for the original `.wav` file in the root folder.

The segment identifiers will be zero-padded to two digits, starting from 01. The `base_name` will be used as part of the file naming convention for subsequent files. You can adjust the `BIN_WIDTH` parameter to change the width of the frequency bins. The x-axis of the graphs will be limited to a maximum frequency of `MAX_FREQUENCY` Hz to ensure consistency across all visualizations.  It's OK to leave these parameters at their default values, which are 10 and 5000.

#### Understanding FFT and Frequency Binning

- **Fast Fourier Transform (FFT)**: The FFT is a mathematical algorithm that transforms a time-domain signal into its constituent frequencies. It helps us understand the frequency content of the audio segments. For a deeper understanding, students are encouraged to look up resources on Fourier Transforms and FFT, as there are many excellent explanations available.

- **Frequency Binning**: After performing the FFT, the resulting frequencies are grouped into "bins." Binning means combining a range of frequencies into a single value, which helps in simplifying and summarizing the data. In this context, each bin represents a small range of frequencies, and the amplitude values within this range are summed up.  You may notice that the resulting frequencies are the center-point of each bin: for a `BIN_WIDTH` of 10 Hz, the bin centers occur at 5 Hz, 15 Hz, 25 Hz and so forth.

By using FFT and frequency binning, we can analyze the frequency characteristics of each tap sound, which is crucial for understanding the acoustic properties of the wooden block being tapped.

By running this cell, you are transforming the audio data into the frequency domain, allowing for detailed frequency analysis and visualization of the tap sounds.

In [ ]:
import os
import json
import numpy as np
import matplotlib.pyplot as plt
from scipy.io import wavfile
from scipy.fft import fft, fftfreq

# Adjustable parameters
BIN_WIDTH = 10  # In Hz, how wide the "bins" are that subdivide the frequency spectrum
MAX_FREQUENCY = 5000  # In Hz, what is the maximum considered frequency

# Function to load the state mapping from a JSON file
def load_state(file_path):
    if os.path.exists(file_path):
        with open(file_path, 'r') as file:
            return json.load(file)
    return {}

# Function to save the state mapping to a JSON file
def save_state(file_path, state):
    with open(file_path, 'w') as file:
        json.dump(state, file, indent=4)

# Function to get the current state of all .wav files in the directory
def get_wav_files_state(directory, state_file):
    state = load_state(state_file)
    wav_files = [f for f in os.listdir(directory) if f.endswith('.wav')]
    for wav_file in wav_files:
        base_name = os.path.splitext(wav_file)[0]
        if base_name not in state:
            state[base_name] = {'state': 'non-split'}
    return state

# Function to perform FFT and bin frequencies
def perform_fft_and_bin(data, sample_rate, bin_width, max_frequency):
    # Convert stereo to mono if necessary
    if len(data.shape) == 2:
        data = np.mean(data, axis=1)

    N = len(data)
    T = 1.0 / sample_rate
    yf = fft(data)
    xf = fftfreq(N, T)[:N//2]
    amplitudes = 2.0 / N * np.abs(yf[0:N//2])

    # Limit frequencies to max_frequency
    xf = xf[xf <= max_frequency]
    amplitudes = amplitudes[:len(xf)]

    # Bin frequencies
    bins = np.arange(0, max_frequency + bin_width, bin_width)
    binned_amplitudes = []

    for i in range(len(bins) - 1):
        bin_mask = (xf >= bins[i]) & (xf < bins[i + 1])
        binned_amplitudes.append({
            'frequency': (bins[i] + bins[i + 1]) / 2,
            'amplitude': np.sum(amplitudes[bin_mask])
        })

    return binned_amplitudes

# Function to select top 10 bins
def select_top_bins(binned_frequencies, top_n=10):
    sorted_bins = sorted(binned_frequencies, key=lambda x: x['amplitude'], reverse=True)
    return sorted_bins[:top_n]

# Function to plot and save bar graph of top 10 binned frequencies
def plot_top_binned_frequencies(binned_frequencies, output_path, bin_width, max_frequency, base_name, segment_id):
    frequencies = [item["frequency"] for item in binned_frequencies]
    amplitudes = [item["amplitude"] for item in binned_frequencies]

    plt.figure(figsize=(10, 6))
    bars = plt.bar(frequencies, amplitudes, width=bin_width, color=plt.cm.viridis(np.linspace(0, 1, len(frequencies))))
    plt.xlabel('Frequency')
    plt.ylabel('Summed Amplitudes')
    plt.title(f'{base_name} {segment_id}: Top 10 Binned Frequencies\n(center point of {bin_width}Hz bin)')
    plt.xlim(0, max_frequency)

    # Add frequency labels above each bar
    for bar, freq in zip(bars, frequencies):
        height = bar.get_height()
        plt.text(bar.get_x() + bar.get_width() / 2, height, f'{freq:.0f}', ha='center', va='bottom')

    plt.tight_layout()
    plt.savefig(output_path)
    plt.close()

# Main function to process the FFT for each segment in the directory
def process_fft_and_bin(directory, state_file, bin_width, max_frequency):
    state = get_wav_files_state(directory, state_file)
    for base_name, info in state.items():
        if info['state'] == 'split':
            subdir = os.path.join(directory, base_name)
            segment_files = [f for f in os.listdir(subdir) if f.endswith('.wav')]
            for segment_id in info['segments']:
                segment_file = f"{base_name}_{segment_id}.wav"
                segment_path = os.path.join(subdir, segment_file)
                sample_rate, data = wavfile.read(segment_path)
                binned_frequencies = perform_fft_and_bin(data, sample_rate, bin_width, max_frequency)
                top_binned_frequencies = select_top_bins(binned_frequencies, top_n=10)

                # Save the entire range of bins to a .json file
                segment_json_path_full = os.path.join(subdir, f"{base_name}_{segment_id}_full.json")
                with open(segment_json_path_full, 'w') as json_file:
                    json.dump(binned_frequencies, json_file, indent=4)
                print(f"Saved {segment_json_path_full}")

                # Save the top 10 binned frequencies to a .json file
                segment_json_path_top = os.path.join(subdir, f"{base_name}_{segment_id}.json")
                with open(segment_json_path_top, 'w') as json_file:
                    json.dump(top_binned_frequencies, json_file, indent=4)
                print(f"Saved {segment_json_path_top}")

                # Plot and save the bar graph of the top 10 frequencies
                plot_path = os.path.join(subdir, f"{base_name}_{segment_id}_fft.png")
                plot_top_binned_frequencies(top_binned_frequencies, plot_path, bin_width, max_frequency, base_name, segment_id)
                print(f"Processed FFT for {segment_file}, saved plot to {plot_path}")

            info['state'] = 'fft'
            save_state(state_file, state)

# Process this step
directory = '.'
state_file = 'wav_files_state.json'
process_fft_and_bin(directory, state_file, BIN_WIDTH, MAX_FREQUENCY)


### Visualization After Step 2: Waveforms and Frequencies

Run the code cell below to generate an interactive tool that allows you to compare two segments by selecting them from dropdown menus. The tool displays the time-amplitude waveform and FFT plot of the top 10 frequencies for the selected segments, along with a table listing the top 10 frequency bins in descending amplitude order.

#### How to Use:



1. **Run the Code**:
   - Execute the code cell to generate the visualizations for the selected segments.

2. **Select Segments**:
   - Use the dropdown menus to select the segments you want to compare. The segments are listed in the format `base_name_segment_id`, where `base_name` is the name of the original audio file and `segment_id` is the segment number (e.g., `"sample_01"`).  Unlike the first visualization tool, running this tool does not require you to alter the code - the dropdowns allow you to select which file you want to show.
   
3. **View Visualizations**:
   - The tool will display two visualizations for each selected segment:
     - **Waveform Plot**: Shows the time-amplitude waveform, allowing you to see the overall shape and intensity of the tap sound.
     - **FFT Plot**: Displays the top 10 frequencies present in the segment, showing the most significant frequency components of the tap sound.

4. **Compare Segments**:
   - Use the visualizations to compare the segments. Look for similarities and differences in the waveforms and frequency plots. Pay attention to:
     - **Waveform Shape**: The shape of the waveform can indicate the nature of the tap, such as its intensity and duration.
     - **Frequency Components**: The FFT plot reveals the dominant frequencies. Comparing these can help identify consistent patterns or anomalies between segments.

#### What to Look For:

- **Consistent Patterns**: Identify any recurring frequency peaks that appear in multiple segments. This can indicate common characteristics of the tap sounds.
- **Anomalies**: Look for any unusual peaks or variations in the waveforms and frequency plots. These could be due to noise or variations in the tap sound.
- **Amplitude Differences**: Compare the amplitude values in the waveforms and FFT plots. Variations in amplitude can provide insights into the intensity and energy of the tap sounds.

By using this tool, you can gain a deeper understanding of the acoustic properties of the tap sounds and how they vary between segments. This interactive visualization helps you analyze and compare the frequency content and waveform shapes of different segments, enhancing your ability to interpret and draw conclusions from the data.

In [ ]:
import ipywidgets as widgets
from IPython.display import display, HTML
from PIL import Image

# Function to load segment data
def load_segment_data(segment):
    base_name, segment_id = segment.rsplit('_', 1)
    subdir = os.path.join('.', base_name)
    waveform_path = os.path.join(subdir, f"{segment}.png")
    fft_path = os.path.join(subdir, f"{segment}_fft.png")
    json_path = os.path.join(subdir, f"{segment}.json")

    with open(json_path, 'r') as file:
        frequencies = json.load(file)

    return waveform_path, fft_path, frequencies

# Function to create the dropdown widget for selecting segments
def create_segment_dropdown(label, segments):
    options = [('', '')] + [(segment, segment) for segment in segments]
    return widgets.Dropdown(options=options, description=label, style={'description_width': 'initial'})

# Function to update the display with selected segment data
def update_display(segment, output_widget):
    if segment:
        waveform_path, fft_path, frequencies = load_segment_data(segment)

        waveform_img = Image.open(waveform_path)
        fft_img = Image.open(fft_path)

        output_widget.clear_output()
        with output_widget:
            display(waveform_img)
            display(fft_img)

            # Display frequency table
            display(HTML(f'<h3>Top 10 Frequency Bins</h3>'))
            table_html = '<table><tr>' + ''.join([f'<th>{bin["frequency"]} Hz</th>' for bin in frequencies]) + '</tr></table>'
            # table_html += '<tr>' + ''.join([f'<td>{bin["amplitude"]:.2f}</td>' for bin in frequencies]) + '</tr></table>'
            display(HTML(table_html))

# Create the interactive tool
def create_comparison_tool(state_file):
    state = load_state(state_file)
    segments = []
    for base_name, info in state.items():
        if 'segments' in info and (info['state'] == 'fft' or info['state'] == 'profiled'):
            segments.extend([f"{base_name}_{seg}" for seg in info['segments']])

    if not segments:
        print("No segments in 'fft' or 'profiled' states found.")
        return

    dropdown1 = create_segment_dropdown('Segment A', segments)
    dropdown2 = create_segment_dropdown('Segment B', segments)

    output1 = widgets.Output()
    output2 = widgets.Output()

    def on_dropdown1_change(change):
        if change['type'] == 'change' and change['name'] == 'value':
            update_display(change['new'], output1)

    def on_dropdown2_change(change):
        if change['type'] == 'change' and change['name'] == 'value':
            update_display(change['new'], output2)

    dropdown1.observe(on_dropdown1_change)
    dropdown2.observe(on_dropdown2_change)

    # Add padding between the two columns
    box = widgets.HBox([widgets.VBox([dropdown1, output1]), widgets.HTML('<h3>vs.</h3>'), widgets.VBox([dropdown2, output2])])
    box.layout.justify_content = 'space-between'

    display(box)

# Process this step
state_file = 'wav_files_state.json'
create_comparison_tool(state_file)


### Step 3: Profiling Tap Sounds

In this step, we will create a statistically useful "profile" of the tap sounds by combining information from all the segments. This involves aggregating the complete set of frequency bins from all segments, applying robust statistical measures to reduce noise and handle outliers, and then saving the full range of frequency bins from the aggregated profile for visualization and analysis.

#### What is Profiling?

- **Profiling**: This process involves combining data from multiple segments to create a single, representative profile. By aggregating the frequency data from all segments, we can identify consistent patterns and reduce the impact of noise or outliers.
- **Goal**: The goal of creating a profile is to have a comprehensive understanding of the frequency characteristics of the tap sounds. This helps in analyzing the acoustic properties and identifying any common features across different segments.

#### How to Use:

1. **Adjust Parameters**:
   - You can adjust the `BIN_WIDTH` and `MAX_FREQUENCY` parameters as needed. These parameters control the width of the frequency bins and the maximum frequency considered during profiling.  It's OK to leave these at their default values, which are 10 and 5000.

2. **Run the Code Cell**:
   - Execute the code cell below to process the segmented audio files and create profiles for each tap sound.

3. **View Output**:
   - The code will print a message indicating that each profile is being processed. After all profiles are created, a final message will be displayed.

By running this cell, you will generate profiles that summarize the frequency characteristics of each tap sound, which will be useful for further analysis and comparison.

In [ ]:
import os
import json
import numpy as np
import matplotlib.pyplot as plt

# Adjustable parameters
BIN_WIDTH = 10  # Hz
MAX_FREQUENCY = 5000  # Hz

# Function to load the state mapping from a JSON file
def load_state(file_path):
    if os.path.exists(file_path):
        with open(file_path, 'r') as file:
            return json.load(file)
    return {}

# Function to save the state mapping to a JSON file
def save_state(file_path, state):
    with open(file_path, 'w') as file:
        json.dump(state, file, indent=4)

# Function to get the current state of all .wav files in the directory
def get_wav_files_state(directory, state_file):
    state = load_state(state_file)
    wav_files = [f for f in os.listdir(directory) if f.endswith('.wav')]
    for wav_file in wav_files:
        base_name = os.path.splitext(wav_file)[0]
        if base_name not in state:
            state[base_name] = {'state': 'non-split'}
    return state

# Function to load frequency bins from sub-files
def load_bins(sub_file):
    with open(sub_file, 'r') as file:
        bins = json.load(file)
    return bins

# Function to aggregate bins from all sub-files
def aggregate_bins(sub_files):
    all_bins = []
    for sub_file in sub_files:
        bins = load_bins(sub_file)
        all_bins.append(bins)

    aggregated_bins = {}
    for bins in all_bins:
        for bin in bins:
            frequency = bin['frequency']
            amplitude = bin['amplitude']
            if frequency not in aggregated_bins:
                aggregated_bins[frequency] = []
            aggregated_bins[frequency].append(amplitude)

    return aggregated_bins

# Function to create a profile from aggregated bins
def create_profile(aggregated_bins):
    profile_bins = []
    for frequency, amplitudes in aggregated_bins.items():
        median_amplitude = np.median(amplitudes)
        profile_bins.append({
            'frequency': frequency,
            'amplitude': median_amplitude
        })
    # Sort by amplitude and select top 10
    profile_bins = sorted(profile_bins, key=lambda x: x['amplitude'], reverse=True)[:10]
    return profile_bins

# Function to save the profile
def save_profile(profile_bins, output_file):
    with open(output_file, 'w') as file:
        json.dump(profile_bins, file, indent=4)

# Function to plot and save bar graph of top 10 binned frequencies
def plot_top_binned_frequencies(binned_frequencies, output_path, bin_width, max_frequency, base_name):
    frequencies = [item["frequency"] for item in binned_frequencies]
    amplitudes = [item["amplitude"] for item in binned_frequencies]

    plt.figure(figsize=(10, 6))
    bars = plt.bar(frequencies, amplitudes, width=bin_width, color=plt.cm.viridis(np.linspace(0, 1, len(frequencies))))
    plt.xlabel('Frequency')
    plt.ylabel('Amplitude')
    plt.title(f'{base_name}: Top 10 Binned Frequencies')
    plt.xlim(0, max_frequency)

    # Add frequency labels above each bar
    for bar, freq in zip(bars, frequencies):
        height = bar.get_height()
        plt.text(bar.get_x() + bar.get_width() / 2, height, f'{freq:.0f}', ha='center', va='bottom')

    plt.tight_layout()
    plt.savefig(output_path)
    plt.close()

# Main function to profile the tap sounds
def profile_tap_sounds(directory, state_file, bin_width, max_frequency):
    state = get_wav_files_state(directory, state_file)
    for base_name, info in state.items():
        if info['state'] == 'fft':
            subdir = os.path.join(directory, base_name)
            segment_files = [os.path.join(subdir, f) for f in os.listdir(subdir) if f.endswith('_full.json')]

            print(f"Processing profile for {base_name}...")
            if len(segment_files) == 0:
                print(f"No segment JSON files found in {subdir}.")
                continue

            aggregated_bins = aggregate_bins(segment_files)
            profile_bins = create_profile(aggregated_bins)

            # Save the profile
            profile_path = os.path.join(subdir, f"{base_name}_profile.json")
            save_profile(profile_bins, profile_path)

            # Plot and save the bar graph
            plot_path = os.path.join(subdir, f"{base_name}_profile.png")
            plot_top_binned_frequencies(profile_bins, plot_path, bin_width, max_frequency, base_name)
            print(f"Profiled tap sounds for {base_name}, saved profile to {profile_path} and plot to {plot_path}")

            info['state'] = 'profiled'
            save_state(state_file, state)

    print("All profiles have been created.")

# Process this step
directory = '.'
state_file = 'wav_files_state.json'
profile_tap_sounds(directory, state_file, BIN_WIDTH, MAX_FREQUENCY)


### Visualization after Step 3: Compare Profiles

This interactive tool allows you to compare the frequency profile FFT images of different tap sound profiles. You can select two profiles from the dropdown menus, and the tool will display their respective FFT images side by side for easy comparison.

#### How to Use:

1. **Run the Code**:
   - Execute the code cell to initialize the interactive visualization tool.

2. **Select Profiles**:
   - Use the dropdown menus labeled "Profile A" and "Profile B" to select the profiles you want to compare. The available profiles are based on the root-level audio files that have been processed and profiled.

3. **View Comparison**:
   - The FFT images of the selected profiles will be displayed side by side. This allows you to visually compare the frequency characteristics of the tap sounds from different profiles.

By using this tool, you can gain insights into the similarities and differences between the frequency profiles of various tap sounds.


In [ ]:
import os
import json
import ipywidgets as widgets
from IPython.display import display, HTML
from PIL import Image

# Function to load profile data
def load_profile_data(profile):
    subdir = os.path.join('.', profile)
    fft_path = os.path.join(subdir, f"{profile}_profile.png")

    return fft_path

# Function to create the dropdown widget for selecting profiles
def create_profile_dropdown(label, profiles):
    options = [('', '')] + [(profile, profile) for profile in profiles]
    return widgets.Dropdown(options=options, description=label, style={'description_width': 'initial'})

# Function to update the display with selected profile data
def update_display(profile, output_widget):
    if profile:
        fft_path = load_profile_data(profile)

        fft_img = Image.open(fft_path)

        output_widget.clear_output()
        with output_widget:
            display(fft_img)

# Create the interactive tool
def create_comparison_tool(state_file):
    state = load_state(state_file)
    profiles = [base_name for base_name, info in state.items() if info['state'] == 'profiled']

    if not profiles:
        print("No profiles in 'profiled' state found.")
        return

    dropdown1 = create_profile_dropdown('Profile A', profiles)
    dropdown2 = create_profile_dropdown('Profile B', profiles)

    output1 = widgets.Output()
    output2 = widgets.Output()

    def on_dropdown1_change(change):
        if change['type'] == 'change' and change['name'] == 'value':
            update_display(change['new'], output1)

    def on_dropdown2_change(change):
        if change['type'] == 'change' and change['name'] == 'value':
            update_display(change['new'], output2)

    dropdown1.observe(on_dropdown1_change)
    dropdown2.observe(on_dropdown2_change)

    # Add padding between the two columns
    box = widgets.HBox([widgets.VBox([dropdown1, output1]), widgets.HTML('<h3>vs.</h3>'), widgets.VBox([dropdown2, output2])])
    box.layout.justify_content = 'space-between'

    display(box)

# Process this step
state_file = 'wav_files_state.json'
create_comparison_tool(state_file)


### Reset Environment

This cell will reset the environment by deleting the subdirectories related to the `.wav` files in the root directory and also deleting the JSON state file. This allows for testing the processing cells in order without deleting and re-creating the runtime.  **Running the code cell below is optional** - it's mostly useful if you want to start over with different parameters like threshold, bin size or segment length.  Note that **this cell does not delete the original sound files** - if you want to use it to start over with a different set of sound files, you will need to delete and/or upload sound files to the root Files folder in Google Colab before re-running Step 1.

In [ ]:
import os
import shutil

# Function to get the current state of all .wav files in the directory
def get_wav_files_state(directory, state_file):
    state = {}
    wav_files = [f for f in os.listdir(directory) if f.endswith('.wav')]
    for wav_file in wav_files:
        base_name = os.path.splitext(wav_file)[0]
        state[base_name] = {'state': 'non-split'}
    return state

# Function to reset the environment
def reset_environment(directory, state_file):
    state = get_wav_files_state(directory, state_file)
    for base_name in state.keys():
        subdir = os.path.join(directory, base_name)
        if os.path.exists(subdir):
            shutil.rmtree(subdir)
            print(f"Deleted directory: {subdir}")
    if os.path.exists(state_file):
        os.remove(state_file)
        print(f"Deleted JSON file: {state_file}")

# Process this step
directory = '.'
state_file = 'wav_files_state.json'
reset_environment(directory, state_file)


## Running this Notebook in Non-Colab Environments

If you need to run this notebook in an environment other than Google Colab, such as Jupyter Notebook or JupyterLab, follow these steps:

### Prerequisites

Ensure you have Python and Jupyter Notebook or JupyterLab installed on your system. You can install Jupyter using `pip` if it's not already installed:

```sh
pip install notebook
```

### Opening the Notebook

1. **Launch Jupyter Notebook or JupyterLab:**
   Open a terminal or command prompt and run:
   ```sh
   jupyter notebook
   ```
   or
   ```sh
   jupyter lab
   ```

2. **Upload the Notebook:**
   - In the Jupyter interface, navigate to the directory where you want to work.
   - Click the "Upload" button and select the `.ipynb` file (e.g., `Tap Testing Day 2 Code.ipynb`).
   - Click "Upload" again to confirm.

3. **Open the Notebook:**
   - Click on the uploaded notebook file to open it.

### Installing Required Libraries

Google Colab comes with many pre-installed libraries, but other Jupyter environments might not have these by default. You'll need to install them manually. The necessary libraries for this notebook include `numpy`, `matplotlib`, `ipywidgets`, `IPython`, `scipy`, and `pydub`.

Open a new code cell at the beginning of the notebook and run the following command to install all required libraries:

```python
!pip install numpy matplotlib ipywidgets IPython scipy pydub
```

### Running the Cells

1. **Run the Setup Cell:**
   - Ensure that the setup cell, which installs any missing libraries, is executed first to install any required packages.
   
2. **Run the Code Cells:**
   - Follow the instructions within the notebook to run each cell in sequence.
   - Adjust the sliders and parameters as instructed, and press the **Show** button to generate the visualizations and play the audio.

### Differences in Library Installations

- **Google Colab:**
  - Comes pre-installed with many scientific and data analysis libraries.
  - Automatically manages dependencies and updates.

- **Jupyter Notebook/JupyterLab:**
  - Requires manual installation of libraries using `pip` or `conda`.
  - May need specific versions of libraries to match the notebook's requirements.

By following these steps, you can successfully run the `Tap Testing Day 2 Code.ipynb` notebook in any Jupyter environment. If you encounter any issues with missing libraries, ensure they are installed using the `pip install` command mentioned above.
